In [1]:
#
# From https://minerl.io/docs/environments/index.html#id9
#
import gym
from gym import spaces
import minerl
import logging
import numpy as np
import collections
import torch
from itertools import chain

C:\Users\liamo\Anaconda3\envs\FallSemester\lib\site-packages\gym\logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
device = torch.device("cuda")

In [3]:
env = gym.make("MineRLNavigateDense-v0") # A MineRLNavigateDense-v0 env

In [4]:
# Run a random agent through the environment
def train(env, agent, config):
    
    num_episodes = config["NUM_EPISODES"]
    episodic_rewards = [0] * num_episodes
    episodic_moves = [0] * num_episodes
    
    for episode in range(num_episodes):
        obs = env.reset()
        done = False
        net_reward = 0
        steps = 0
        
        obs["pov"] = obs["pov"].reshape(3,64,64)
        obs["pov"] = torch.from_numpy(obs["pov"]).float().to(device).unsqueeze(0)
        obs["compassAngle"] = torch.from_numpy(obs["compassAngle"]).float().to(device).unsqueeze(0)
                                      
        while not done:
            # this is only outputting the camera controls
            camera_action = agent.step(obs)
            
            print(camera_action)
    
            env_action = {}
            
            env_action["camera"] = [0, camera_action.detach().cpu().item()]
            env_action["attack"] = 0
            env_action["back"] = 0
            env_action["forward"] = 1
            env_action["jump"] = 1
            env_action["left"] = 0
            env_action["place"] = "none"
            env_action["right"] = 0
            env_action["sneak"] = 0
            env_action["sprint"] = 0
    
            steps = steps + 1
            next_obs, reward, done, info = env.step(env_action)
            
            next_obs["pov"] = next_obs["pov"].reshape(3,64,64)
            next_obs["pov"] = torch.from_numpy(next_obs["pov"]).float().to(device).unsqueeze(0)
            next_obs["compassAngle"] = torch.from_numpy(next_obs["compassAngle"]).float().to(device).unsqueeze(0)
    
            camera_action = camera_action.unsqueeze(0)
            reward = torch.tensor([reward], device=device)
            done = torch.tensor([done], device=device).int()
            
            
            agent.memory.store_transition(obs, camera_action, next_obs, reward, done)
            if steps % config["EVAL_INTERVAL"] == 0:
                    agent.evaluate()
            obs = next_obs     
            episodic_rewards[episode] += reward
            episodic_moves[episode] += 1
    
        print(episode)
        print("reward", episodic_rewards[episode])
    return episodic_rewards, episodic_moves        
     
    # Do something

In [5]:
%run SoftAC.ipynb
agent_config = {
    "ALPHA": .6,
    "GAMMA": .9,
    "POLYAK": .99,
    "LEARNING_RATE": .00001,
    "MAX_MEMORY": 10000,
    "BATCH_SIZE": 128
}
agent = SoftACAgent(env, agent_config)

C:\Users\liamo\Anaconda3\envs\FallSemester\lib\site-packages\gym\logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [6]:
train_config = {
    "EVAL_INTERVAL": 10,
    "NUM_EPISODES": 25
}
rew, moves = train(env, agent, train_config)

tensor([[28.6137]], device='cuda:0')
tensor([[29.4833]], device='cuda:0')
tensor([[29.7717]], device='cuda:0')
tensor([[29.8633]], device='cuda:0')
tensor([[29.8790]], device='cuda:0')
tensor([[29.8393]], device='cuda:0')
tensor([[29.6778]], device='cuda:0')
tensor([[29.0891]], device='cuda:0')
tensor([[26.5913]], device='cuda:0')
tensor([[13.2497]], device='cuda:0')
tensor([[29.9282]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-29.9998]], device='cuda:0')
tensor([[29.9898]], device='cuda:0')
tensor([[29.9794]], device='cuda:0')
tensor([[29.9645]], device='cuda:0')
tensor([[29.9442]], device='cuda:0')
tensor([[29.9115]], device='cuda:0')
tensor([[29.8535]], device='cuda:0')
tensor([[29.7292]], device='cuda:0')
tensor([[29.4334]], device='cuda:0')
tensor([[28.6349]], device='cuda:0')
tensor([[26.3717]], device='cuda:0')
tensor([[19.7627]], device='cuda:0')
tensor([[-29.9965]], device='cuda:0')
tensor([[-29.7462]], device='cuda:0')
tenso

tensor([[29.9596]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[29.7239]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[28.0501]], device='cuda:0')
tensor([[-29.9999]], device='cuda:0')
tensor([[-26.0652]], device='cuda:0')
tensor([[29.9661]], device='cuda:0')
tensor([[29.9723]], device='cuda:0')
tensor([[29.9417]], device='cuda:0')
tensor([[29.8995]], device='cuda:0')
tensor([[29.7917]], device='cuda:0')
tensor([[29.5955]], device='cuda:0')
tensor([[29.1441]], device='cuda:0')
tensor([[28.0624]], device='cuda:0')
tensor([[25.4303]], device='cuda:0')
tensor([[11.1291]], device='cuda:0')
tensor([[29.8704]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[29.3711]], device='cuda:0')
tensor([[29.9992]], device='cuda:0')
tensor([[27.9058]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[-28.5981]], device='cuda:0')
tensor([[-29.9998]], device='cuda:0')
tensor([[29.9877]], device='cuda:0')
tensor([[-29.9

tensor([[-19.4121]], device='cuda:0')
tensor([[-29.6693]], device='cuda:0')
tensor([[30.0000]], device='cuda:0')
tensor([[-30.0000]], device='cuda:0')
tensor([[-30.0000]], device='cuda:0')
tensor([[30.0000]], device='cuda:0')
tensor([[29.9995]], device='cuda:0')
tensor([[-29.9985]], device='cuda:0')
tensor([[6.8912]], device='cuda:0')
tensor([[19.4655]], device='cuda:0')
tensor([[20.3216]], device='cuda:0')
tensor([[20.2320]], device='cuda:0')
tensor([[18.0150]], device='cuda:0')
tensor([[29.9737]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[29.7949]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-29.9989]], device='cuda:0')
tensor([[22.6264]], device='cuda:0')
tensor([[29.9997]], device='cuda:0')
tensor([[29.9983]], device='cuda:0')
tensor([[27.7971]], device='cuda:0')
tensor([[27.3286]], device='cuda:0')
tensor([[26.7189]], device='cuda:0')
tensor([[25.9031]], device='cuda:0')
tensor([[24.8338]], device='cuda:0')
tensor(

tensor([[13.1692]], device='cuda:0')
tensor([[13.8435]], device='cuda:0')
tensor([[15.6497]], device='cuda:0')
tensor([[17.3280]], device='cuda:0')
tensor([[11.9217]], device='cuda:0')
tensor([[29.9999]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[29.6553]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[29.9999]], device='cuda:0')
tensor([[-29.9994]], device='cuda:0')
tensor([[29.9532]], device='cuda:0')
tensor([[16.2639]], device='cuda:0')
tensor([[0.3628]], device='cuda:0')
tensor([[1.5872]], device='cuda:0')
tensor([[2.5588]], device='cuda:0')
tensor([[3.2782]], device='cuda:0')
tensor([[3.7822]], device='cuda:0')
tensor([[4.1164]], device='cuda:0')
tensor([[4.3076]], device='cuda:0')
tensor([[2.0059]], device='cuda:0')
tensor([[2.0837]], device='cuda:0')
tensor([[2.1389]], device='cuda:0')
tensor([[2.1623]], device='cuda:0')
tensor([[2.2260]], device='cuda:0')
tensor([[2.2957]], device='cuda:0')
tensor([[2.4291]], devic

tensor([[10.8225]], device='cuda:0')
tensor([[8.1458]], device='cuda:0')
tensor([[6.5917]], device='cuda:0')
tensor([[6.2951]], device='cuda:0')
tensor([[7.2933]], device='cuda:0')
tensor([[9.3056]], device='cuda:0')
tensor([[12.1749]], device='cuda:0')
tensor([[14.5592]], device='cuda:0')
tensor([[25.2264]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[-29.5005]], device='cuda:0')
tensor([[28.6676]], device='cuda:0')
tensor([[-17.2999]], device='cuda:0')
tensor([[-29.8862]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[28.6696]], device='cuda:0')
tensor([[-29.9499]], device='cuda:0')
tensor([[-30.]], device='cuda:0')
tensor([[-30.0000]], device='cuda:0')
tensor([[29.9993]], device='cuda:0')
tensor([[-29.9093]], device='cuda:0')
tensor([[-16.7869]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[30.]], device='cuda:0')
tensor([[29.9991]], device='cu

...

tensor([[-27.1054]], device='cuda:0')
tensor([[10.0038]], device='cuda:0')
tensor([[-28.3713]], device='cuda:0')
tensor([[12.1415]], device='cuda:0')
tensor([[-19.2122]], device='cuda:0')
tensor([[22.4780]], device='cuda:0')
tensor([[-16.3604]], device='cuda:0')
tensor([[-21.9665]], device='cuda:0')
tensor([[-12.7492]], device='cuda:0')
tensor([[-25.1422]], device='cuda:0')
tensor([[-24.7597]], device='cuda:0')
tensor([[-22.0413]], device='cuda:0')
tensor([[4.2390]], device='cuda:0')
tensor([[1.2958]], device='cuda:0')
tensor([[18.8546]], device='cuda:0')
tensor([[21.3734]], device='cuda:0')
tensor([[25.4240]], device='cuda:0')
tensor([[-12.7034]], device='cuda:0')
tensor([[9.9030]], device='cuda:0')
tensor([[23.6769]], device='cuda:0')
tensor([[22.2254]], device='cuda:0')
tensor([[-24.6090]], device='cuda:0')
tensor([[-20.5292]], device='cuda:0')
tensor([[-27.0892]], device='cuda:0')
tensor([[-12.4045]], device='cuda:0')
tensor([[-25.0310]], device='cuda:0')
tensor([[-24.9897]], devic

tensor([[-25.9334]], device='cuda:0')
tensor([[-18.7043]], device='cuda:0')
tensor([[11.6254]], device='cuda:0')
tensor([[6.0730]], device='cuda:0')
tensor([[-14.6842]], device='cuda:0')
tensor([[24.0135]], device='cuda:0')
tensor([[-11.7657]], device='cuda:0')
tensor([[-14.7484]], device='cuda:0')
tensor([[3.9648]], device='cuda:0')
tensor([[9.1158]], device='cuda:0')
tensor([[-0.5075]], device='cuda:0')
tensor([[-21.7044]], device='cuda:0')
tensor([[-25.8238]], device='cuda:0')
tensor([[13.4056]], device='cuda:0')
tensor([[20.8448]], device='cuda:0')
tensor([[-20.0728]], device='cuda:0')
tensor([[-16.9118]], device='cuda:0')
tensor([[-9.2042]], device='cuda:0')
tensor([[-11.7766]], device='cuda:0')
tensor([[-24.4739]], device='cuda:0')
tensor([[12.1767]], device='cuda:0')
tensor([[22.9494]], device='cuda:0')
tensor([[-25.1587]], device='cuda:0')
tensor([[9.8305]], device='cuda:0')
tensor([[-26.4839]], device='cuda:0')
tensor([[-21.6262]], device='cuda:0')
tensor([[-28.1657]], device=

tensor([[10.4749]], device='cuda:0')
tensor([[1.2941]], device='cuda:0')
tensor([[-4.2524]], device='cuda:0')
tensor([[-5.6255]], device='cuda:0')
tensor([[-28.1462]], device='cuda:0')
tensor([[-29.5343]], device='cuda:0')
tensor([[-11.3829]], device='cuda:0')
tensor([[-15.1141]], device='cuda:0')
tensor([[21.4001]], device='cuda:0')
tensor([[-4.6090]], device='cuda:0')
tensor([[10.7856]], device='cuda:0')
tensor([[3.2242]], device='cuda:0')
tensor([[-1.6205]], device='cuda:0')
tensor([[-4.3026]], device='cuda:0')
tensor([[16.7747]], device='cuda:0')
tensor([[-18.7217]], device='cuda:0')
tensor([[-15.1965]], device='cuda:0')
tensor([[-11.2102]], device='cuda:0')
tensor([[16.5260]], device='cuda:0')
tensor([[-11.0099]], device='cuda:0')
tensor([[-13.6725]], device='cuda:0')
tensor([[-20.5111]], device='cuda:0')
tensor([[-16.3024]], device='cuda:0')
tensor([[-25.4730]], device='cuda:0')
tensor([[-21.2764]], device='cuda:0')
tensor([[-14.5768]], device='cuda:0')
tensor([[6.8031]], device=

tensor([[3.0799]], device='cuda:0')
tensor([[-15.2580]], device='cuda:0')
tensor([[-20.0477]], device='cuda:0')
tensor([[4.9154]], device='cuda:0')
tensor([[4.5356]], device='cuda:0')
tensor([[-7.6651]], device='cuda:0')
tensor([[21.5772]], device='cuda:0')
tensor([[-27.5680]], device='cuda:0')
tensor([[-14.2045]], device='cuda:0')
tensor([[-12.3732]], device='cuda:0')
tensor([[-14.6653]], device='cuda:0')
tensor([[-4.2932]], device='cuda:0')
tensor([[18.2494]], device='cuda:0')
tensor([[-26.9583]], device='cuda:0')
tensor([[-17.0884]], device='cuda:0')
tensor([[21.6518]], device='cuda:0')
tensor([[3.1635]], device='cuda:0')
tensor([[-7.0755]], device='cuda:0')
tensor([[-24.8879]], device='cuda:0')
tensor([[2.2824]], device='cuda:0')
tensor([[-14.0463]], device='cuda:0')
tensor([[6.4074]], device='cuda:0')
tensor([[7.8460]], device='cuda:0')
tensor([[-26.2522]], device='cuda:0')
tensor([[-20.8231]], device='cuda:0')
tensor([[5.4867]], device='cuda:0')
tensor([[-0.2302]], device='cuda:0

KeyboardInterrupt: 

In [ ]:
env.close()

In [ ]:
import matplotlib.pyplot as plt
plt.plot(rew)
plt.show()

In [ ]:
sum(rew)/len(rew)